# PTAC Current Spikes

In [1]:
import os
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
# turn off scientific notation  in pandas
pd.set_option('display.float_format', lambda x: '%.3f' % x)

# set max columns and rows to display
pd.set_option('display.max_columns', 500)
pd.set_option('display.max_rows', 500)

In [2]:
circuit_df = pd.read_excel('ALG_ptac_inventory.xlsx').set_index('id')
circuit_df['full_address'] = circuit_df.apply(lambda s: f"{s['address1']}_{s['city']}_{s['state']}", axis=1)

for csv in os.listdir('data'):
    if csv == 'rmsCurrent.csv':
        print(csv)

        current_df = pd.read_csv(f'data/{csv}', 
                         parse_dates=[0], 
                         index_col=0)
        
        current_df.index = current_df.index.tz_localize('UTC').tz_convert('America/New_York')
        
    elif csv == 'powerFactor.csv':
        print(csv)

        power_factor_df = pd.read_csv(f'data/{csv}', 
                         parse_dates=[0], 
                         index_col=0)
        
        power_factor_df.index = power_factor_df.index.tz_localize('UTC').tz_convert('America/New_York')
        


rmsCurrent.csv
powerFactor.csv


In [3]:
ptacs_df = current_df.groupby([circuit_df['full_address'], circuit_df['description']], axis=1).sum()
ptacs_pf_df = power_factor_df.groupby([circuit_df['full_address'], circuit_df['description']], axis=1).mean()

In [13]:
# find usually high current spikes

abberations = []

for unit in ptacs_df.columns:
    highestCurrent = ptacs_df[unit].max()
    highestCurrentTime = ptacs_df[unit].idxmax()

    current99 = ptacs_df[unit].quantile(0.999)

    if highestCurrent > current99 * 1.5:
        abberations.append((unit, highestCurrent, highestCurrentTime))


fig = make_subplots(rows=len(abberations), cols=1,
                    specs=[[{"secondary_y": True}]]*len(abberations))

for i, abberation in enumerate(abberations):
    unit, highestCurrent, highestCurrentTime = abberation
    startTime = highestCurrentTime - pd.Timedelta('3 day')
    endTime = highestCurrentTime + pd.Timedelta('3 day')

    fig.add_trace(go.Scatter(x=ptacs_df[startTime:endTime].index, 
                             y=ptacs_df[unit][startTime:endTime],
                             showlegend=False,
                             line=dict(width=1, color='blue'),
                             name=unit[0] + unit[1]), row=i+1, col=1)
    
    fig.add_trace(go.Scatter(x=ptacs_pf_df[startTime:endTime].index,
                                y=ptacs_pf_df[unit][startTime:endTime],
                                showlegend=False,
                                line=dict(width=.5, color='grey'),
                                name=unit[0] + unit[1]), 
                                secondary_y=True, 
                                row=i+1, 
                                col=1)
    
    fig.add_trace(go.Scatter(x=[highestCurrentTime], y=[highestCurrent],
                             mode='markers',
                             marker=dict(color='red', size=10),
                             name='Highest Current',
                             showlegend=False), row=i+1, col=1)
    

    fig.update_yaxes(title_text="Current (A)", row=i+1, col=1)
    fig.update_yaxes(title_text="Power Factor", row=i+1, col=1, secondary_y=True)
    

fig.update_layout(height=300*len(abberations), 
                  width=800, 
                  title_text="Current and Power Factor",
                  template='simple_white')



In [5]:
startTime

Timestamp('2022-04-30 21:35:00-0400', tz='America/New_York')